# Sequential testing от Netflix

На моделировании посмотрим, сохраняет ли заданную ошибку первого рода данный подход с постоянным мониторингом, какая у него мощность и сравним его с подглядыванием при обычном fixed-horizon подходе.

In [1]:
import numpy as np
import scipy.stats as stats
from scipy.special import loggamma, gammaln, xlogy
from tqdm import tqdm
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import warnings
warnings.filterwarnings("ignore")

In [3]:
def sequential_p_value(counts, assignment_probabilities, dirichlet_alpha=None):
    """
    Compute the sequential p-value for given counts and assignment probabilities.
    Lindon, Michael, and Alan Malek.
    "Anytime-Valid Inference For Multinomial Count Data."
    In Advances in Neural Information Processing Systems, 2022
    https://openreview.net/pdf?id=a4zg0jiuVi
    Parameters
    ----------
    counts : array like
        The observed counts in each treatment group.
    assignment_probabilities : array like
        The assignment probabilities to each treatment group.
    dirichlet_alpha : array like, optional
        The Dirichlet mixture parameter.
    Returns
    -------
    float
        The sequential p-value.
    """
    counts = np.array(counts)
    assignment_probabilities = np.array(assignment_probabilities)
    if dirichlet_alpha is None:
        dirichlet_alpha = 100 * assignment_probabilities
    else:
        dirichlet_alpha = np.array(dirichlet_alpha)
    lm1 = (
        loggamma(counts.sum() + 1)
        - loggamma(counts + 1).sum()
        + loggamma(dirichlet_alpha.sum())
        - loggamma(dirichlet_alpha).sum()
        + loggamma(dirichlet_alpha + counts).sum()
        - loggamma((dirichlet_alpha + counts).sum())
    )
    lm0 = gammaln(counts.sum() + 1) + np.sum(
        xlogy(counts, assignment_probabilities) - gammaln(counts + 1), axis=-1
    )
    return min(1, np.exp(lm0 - lm1))

Реализуем насколько функций.

На моделировании будем проверять гипотезу о равенстве средних распределения Бернулли, то есть конверсий.


*   *run_experiment* - запускает моделирвоание
*   *apply_sequential_testing* - имитирует процедуру постоянного мониторинга для двух массивов с данными (единички и нолики - была ли конверсия или нет)




In [25]:
def run_experiment(simulations=5000, trials=2000, alpha=0.05, conversion_rate_A=0.1, conversion_rate_B=0.1):
    """
    Запускает моделирование с указанным числом симуляций, считает
    процент ложных срабатываний (FPR) для AA теста и мощность (Power) для AB теста.

    Parameters:
    simulations (int): Количество симуляций.
    trials (int): Количество наблюдений в каждой группе.
    alpha (float): Уровень значимости.
    conversion_rate_A (float): Конверсия группы A.
    conversion_rate_B (float): Конверсия группы B.

    Returns:
    tuple: Процент ложных срабатываний (для AA теста) или мощность (для AB теста)
    для chi-square теста и последовательного p-значения.
    """
    chi_sq_results = 0
    sequential_results = 0

    for _ in tqdm(range(simulations)):
        counts_A = np.random.binomial(1, conversion_rate_A, trials)
        counts_B = np.random.binomial(1, conversion_rate_B, trials)

        observed_A = np.sum(counts_A)
        observed_B = np.sum(counts_B)

        observed = np.array([observed_A, observed_B])
        expected = np.array([sum(observed) / 2, sum(observed) / 2])

        chi2, p = stats.chisquare(observed, expected)
        _, avpv = apply_sequential_testing(counts_A, counts_B)

        if p < alpha:
            chi_sq_results += 1

        if avpv < alpha:
            sequential_results += 1

    chi_sq_rate = chi_sq_results / simulations
    sequential_rate = sequential_results / simulations

    return chi_sq_rate, sequential_rate


def apply_sequential_testing(counts_A, counts_B, alpha=0.05):
    """
    Применяет последовательное тестирование. Возвращает 1, если p-значение
    ниже alpha на каком-либо этапе, иначе возвращает 0.

    Аргументы:
    counts_A (array): Наблюдения в группе A.
    counts_B (array): Наблюдения в группе группы B.
    alpha (float): Уровень значимости для тестов.

    Возвращает:
    tuple: (Результат теста: 1 или 0, Итоговое p-value)
    """
    n = len(counts_A)
    cumulative_counts_A = np.cumsum(counts_A)
    cumulative_counts_B = np.cumsum(counts_B)

    cumulative_counts = np.vstack((cumulative_counts_A, cumulative_counts_B)).T
    previous_p_avpv = 1

    for i in range(n):
        observed = cumulative_counts[i]

        avpv = sequential_p_value(observed, [0.5, 0.5])

        avpv = min(previous_p_avpv, avpv)
        previous_p_avpv = avpv

        if avpv < alpha:
            return 1, avpv

    return 0, avpv


## A/A test

In [26]:
# Запускаем моделирование A/A тестов
fpr_chi_sq, fpr_sequential = run_experiment(
    simulations=2000,
    trials=2000,
    alpha=0.05,
    conversion_rate_A=0.1,
    conversion_rate_B=0.1  # Эффекта нет
)
print("\nA/A tests:")
print(f"False Positive Rate, chi-sq: {np.round(fpr_chi_sq, 4)}")
print(f"False Positive Rate, always valid p-value: {np.round(fpr_sequential, 4)}")

100%|██████████| 2000/2000 [03:50<00:00,  8.68it/s]


A/A tests:
False Positive Rate, chi-sq: 0.0435
False Positive Rate, always valid p-value: 0.005


При применении последовательного тестирование fpr даже меньше заданного, вероятно на это влияет параметр dirichlet_alpha, но цели мы достигаем.

## A/B test

In [27]:
# Запускаем моделирование A/B тестов
power_chi_sq, power_sequential = run_experiment(
    simulations=2000,
    trials=2000,
    alpha=0.05,
    conversion_rate_A=0.1,
    conversion_rate_B=0.13  # Добавляем эффект
)
print("\nA/B tests")
print(f"Power, chi-sq: {power_chi_sq}")
print(f"Power, always valid p-value: {power_sequential}")

100%|██████████| 2000/2000 [02:46<00:00, 12.03it/s]


A/B tests
Power, chi-sq: 0.812
Power, always valid p-value: 0.5285


При этом мощность такого подхода ожидаемо ниже. Но если по данному методу тест не красится раньше расчитанного периода при последовательном мониторинге, то в конце мы просто применяем обычный тест и ничего не теряем в мощности. А большие эффекты можем детектить раньше и стопать для них тесты быстрее, а не ждать оконания расчитанного размера выборки.  

## Моделируем ошибку подглядывания

Будем специально подглядывать и в fixed-horizon подходе и смотреть, как сильно увеличится ошибка первого рода для него.

In [55]:
import numpy as np
from scipy import stats
from scipy.special import loggamma, gammaln, xlogy
from tqdm import tqdm

# Параметры моделирования
n_simulations = 1000
n_trials = 2000
alpha = 0.05

# Параметры распределения
conversion_rate_A = 0.1
conversion_rate_B = 0.1

false_positives = {}
false_positives_avpv = {}

p_values = {}
aw_p_values = {}

for k in tqdm(range(n_simulations)):
    counts_A = np.random.binomial(1, conversion_rate_A, n_trials)
    counts_B = np.random.binomial(1, conversion_rate_B, n_trials)

    false_positives[k] = 0
    false_positives_avpv[k] = 0

    p_values[k] = []
    aw_p_values[k] = []

    previous_p_avpv = 1

    for i in range(n_trials):
        observed_A = np.sum(counts_A[:i+1])
        observed_B = np.sum(counts_B[:i+1])

        observed = np.array([observed_A, observed_B])
        expected = np.array([sum(observed) / 2, sum(observed) / 2])

        chi2, p = stats.chisquare(observed, expected)

        avpv = sequential_p_value(observed, [0.5, 0.5])
        avpv = min(previous_p_avpv, avpv)
        previous_p_avpv = avpv

        if p < alpha:
            if conversion_rate_A == conversion_rate_B:
                false_positives[k] = 1

        if avpv < alpha:
            if conversion_rate_A == conversion_rate_B:
                false_positives_avpv[k] = 1

        p_values[k].append(p)
        aw_p_values[k].append(avpv)


false_positive_rate = sum(false_positives.values()) / n_simulations
false_positive_rate_avpv = sum(false_positives_avpv.values()) / n_simulations

print('\n')
print(f"False Positive Rate chi-sq: {false_positive_rate}")
print(f"False Positive Rate sequential: {false_positive_rate_avpv}")


100%|██████████| 1000/1000 [11:28<00:00,  1.45it/s]



False Positive Rate chi-sq: 0.367
False Positive Rate sequential: 0.006


Ождиаемо, при подглядывании в fixed-horizon мы совершаем ошибку первого рода почти в 40% вместо ожидаемых 5%. При этом в последовательном тестировании все хорошо.

In [42]:
simulation_index = 5  # Номер симуляции

p_vals = p_values[simulation_index]
aw_p_vals = aw_p_values[simulation_index]
trials = list(range(len(p_vals)))

fig = go.Figure()
fig.add_trace(go.Scatter(x=trials, y=p_vals, mode='lines', name='Chi-square p-value'))
fig.add_trace(go.Scatter(x=trials, y=aw_p_vals, mode='lines', name='Sequential p-value'))
fig.add_trace(go.Scatter(x=trials, y=[alpha] * len(trials), mode='lines', name='Alpha threshold', line=dict(color='red', dash='dash')))
fig.update_layout(
    title="Сравнение Fixed Horizon and Sequential p-values",
    xaxis_title="Trial",
    yaxis_title="p-value",
    legend_title="Legend",
    template="plotly_white"
)
fig.show()


In [56]:
n_simulations_to_plot = 100 # отрисуем первые  100 симулций


fig = go.Figure()

for k in range(n_simulations_to_plot):
    fig.add_trace(go.Scatter(x=list(range(len(p_values[k]))), y=p_values[k],
                             mode='lines', line=dict(color='blue', width=1),
                             opacity=0.4, showlegend=False))

for k in range(n_simulations_to_plot):
    fig.add_trace(go.Scatter(x=list(range(len(aw_p_values[k]))), y=aw_p_values[k],
                             mode='lines', line=dict(color='red', width=1),
                             opacity=0.99, showlegend=False))

fig.add_trace(go.Scatter(x=list(range(len(p_values[0]))), y=[0.05] * len(p_values[0]),
                         mode='lines', name='Alpha = 0.05',
                         line=dict(color='red', dash='dash')))

fig.update_layout(
    title="Сравнение классического подхода и последовательного тестирования",
    xaxis_title="Trial",
    yaxis_title="p-value",
    template="plotly_white",
    height=750,
    #width=1000
)

fig.show()


### To do


Такие тесты позволяют стопать раньше, только если эффекты действительно большие. Как видно было на моделирвоании AB теста, при эффекте, который согласно рассчитанному размеру выборки можно задетектить в 80% (т.е. была задана ошибка второго рода 20%), если в конце учитывать именно расчетанное p-value методом от нетфликс, мощность сильно меньше. Интересно поисследовать, насколько в среднем получается ускорять тесты.  

*   Можно взять несколько конверсий и размеров эффектов. Запустить моделирование и посмотреть, какая мощность у последовательного тестирования и насколько быстрее получается стопать тесты.

*   Дополнительно можно исследовать, как параметр dirichlet_alpha влияет на это.

